In [1]:
from sentence_transformers import SentenceTransformer
from umap import UMAP
from hdbscan import HDBSCAN
from sklearn.feature_extraction.text import CountVectorizer
import pandas as pd
import numpy as np
from bertopic import BERTopic
from bertopic.vectorizers import ClassTfidfTransformer
from bertopic.representation import KeyBERTInspired
from sklearn.cluster import KMeans, Birch
from sklearn.feature_extraction.text import TfidfVectorizer

pd.set_option('max_colwidth', None)
pd.set_option('display.width', None)

# 1. Load data

In [2]:
crashes = pd.read_csv('data/clean_crashes.csv', 
                      usecols=['Date', 'Location', 'Operator', 'Type', 'Aboard', 'Fatalities', 'Ground', 'Summary'])

crashes.tail(2)

Date                                      Location  \
4829  2009-06-07  Near Port Hope Simpson, Newfoundland, Canada   
4830  2009-06-08             State of Arunachal Pradesh, India   

                         Operator                              Type  Aboard  \
4829                   Strait Air  Britten-Norman BN-2A-27 Islander     1.0   
4830  Military - Indian Air Force                     Antonov An-32    13.0   

      Fatalities  Ground  \
4829         1.0     0.0   
4830        13.0     0.0   

                                                                                                                     Summary  
4829              The air ambulance crashed into hills while attempting to land in heavy fog about 4 miles from the airport.  
4830  The military transport went missing while en route and might have crashed due to heavy rain in the mountainous region.

In [3]:
from spacy.lang.en.stop_words import STOP_WORDS as stop_list
# stop.update(['crashed', 'crash', 'aircraft', 'airplane', 'plane', 'pilot', 'flight', 'cargo', 'accident', 'seaplane', 'mail', 'postal', 'helicopter', 'baggage', 'cessna'])
stop_list.update(['aircraft', 'crashed', 'plane', 'flight', 'airplane', 'wreckage', 'cessna'])
stop_list = list(stop_list)

# 2. Prepare embeddings

In [4]:
# Step 1 - Extract embeddings
embedding_model = SentenceTransformer("all-MiniLM-L6-v2")
embeddings = embedding_model.encode(crashes.Summary.values, show_progress_bar=True)

Batches:   0%|          | 0/151 [00:00<?, ?it/s]

# 3. Clulster data

In [5]:
# Step 2 - Reduce dimensionality
umap_model = UMAP(n_neighbors=300, n_components=10, min_dist=0.00, random_state=42)

# Step 3 - Cluster reduced embeddings
# hdbscan_model = HDBSCAN(min_cluster_size=30, min_samples=1, metric='euclidean', 
#                         cluster_selection_method='eom', prediction_data=True)
hdbscan_model = KMeans(n_clusters=20, max_iter=1000, random_state=42)
# hdbscan_model = Birch(n_clusters=30)

# Step 4 - Tokenize topics
vectorizer_model = CountVectorizer(stop_words=stop_list, min_df=10, ngram_range=(1, 2))
# vectorizer_model = TfidfVectorizer(stop_words=stop)

# Step 5 - Create topic representation
ctfidf_model = ClassTfidfTransformer(reduce_frequent_words=True, bm25_weighting=True)

# Step 6 - (Optional) Fine-tune topic representations with 
# a `bertopic.representation` model
representation_model = KeyBERTInspired()

In [6]:
topic_model = BERTopic(

  embedding_model=embedding_model,
  umap_model=umap_model,
  hdbscan_model=hdbscan_model,
  vectorizer_model=vectorizer_model,
  ctfidf_model=ctfidf_model,
  representation_model=representation_model,
    
  top_n_words=10,
  verbose=True
)

topics, probs = topic_model.fit_transform(crashes.Summary.to_list(), embeddings)

2024-03-29 12:59:42,730 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-03-29 13:00:20,801 - BERTopic - Dimensionality - Completed ✓
2024-03-29 13:00:20,802 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-03-29 13:00:21,121 - BERTopic - Cluster - Completed ✓
2024-03-29 13:00:21,124 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-03-29 13:00:27,843 - BERTopic - Representation - Completed ✓


In [7]:
topic_model.get_topic_info()[['Topic', 'Count', 'Representation']]

Topic  Count  \
0       0    424   
1       1    380   
2       2    359   
3       3    356   
4       4    356   
5       5    338   
6       6    307   
7       7    305   
8       8    288   
9       9    242   
10     10    225   
11     11    219   
12     12    210   
13     13    204   
14     14    133   
15     15    125   
16     16    118   
17     17    118   
18     18     82   
19     19     42   

                                                                                                                                                     Representation  
0                                    [emergency landing, exploded, shortly takeoff, landed, caught fire, explosion, crash, landing, survived, attempting emergency]  
1                                        [pilot failure, safe altitude, flew, flying, mountains, altitude, mountain, mountainous terrain, mountainous, error pilot]  
2                                             [cause accident, accident, failure pilot, contributing accident, stalled, maneuver, flying, caused, aborted, failure]  
3                         [pilot failure, cargo, accident, lost altitude, flew, runway attempting, contributing accident, pilot command, failure maintain, takeoff]  
4                                        [engine failure, crash, emergency landing, shortly takeoff, malfunction, fatigue, broke, forced landing, failure, engines]  
5                                                 [crash landed, crash, mountainous terrain, mountainous, mountains, mountain, terrain, survived, poor weather, mt]  
6                            [pilot failed, landing attempt, pilot error, crew error, landing approach, failure crew, pilots, flying, disoriented, missed approach]  
7                                                                        [crash, accident, survived, crashing, flying, pilot reported, pilots, died, jet, ran fuel]  
8   [engine failure, cause accident, pilot failed, failure pilot, mechanical failure, emergency landing, failure captain, malfunctioning, failure, shortly takeoff]  
9                          [landing attempt, pilot attempted, runway attempting, landed, landing, struck ground, hit ground, caught fire, end runway, short runway]  
10                           [crash landed, severe turbulence, crash, thunderstorm, thunderstorms, emergency landing, snowstorm, storm, lost altitude, bad weather]  
11                                              [shortly takeoff, ocean, sank, engine failure, sea, flying, taking pilot, survivors, pilot reported, losing engine]  
12                                                 [flew, pilot attempted, struck trees, rain fog, flying, adverse weather, pilot error, collided trees, rain, vfr]  
13                                                     [pilot error, flew, airborne, rain fog, error pilot, flying, severe turbulence, heavy fog, heavy rain, rain]  
14                                                                 [failure pilot, pilots, landed, survived, collided, collision, flying, jet, accident, air force]  
15                                                        [disappeared, en route, route, missing, encountered, appeared, recovered, departed, unknown, destination]  
16                                                                [emergency landing, air force, landed, shot, radar, helicopter, crash landed, military, jet, air]  
17                                                 [helicopter, pilot failure, crash, accident, contributing accident, crashing, flying, exploded, failure, caused]  
18                                                             [flew, flying, mountain, flying low, fly, drifted, terrain, rising terrain, descended, poor weather]  
19                          [crash landed, pilot failure, emergency landing, crash, killed pilot, landed, crashing, pilot error, error pilot, attempting emergency]

In [8]:
crashes['Cluster'] = topics

## 3.1. Get topic stats

In [ ]:
index = 0
topic_model.get_topic_info(index)

In [ ]:
crashes[crashes.Cluster == index][['Summary']].head(50)

# 4. Label topics

In [19]:
topic_model.set_topic_labels({19: "Mail plane", 18: "Mountains", 17: "Helicopter", 16: "Shot down", 
                              15: "Disappeared en route", 14: "Midair collision", 13: "Fog", 
                              12: "Weather conditions", 11: "Crashed into sea", 10: "Weather / landing", 
                              9: "Landing attempt", 8: "Engine failure", 7: "Crash", 6: "Pilot error", 
                              5: "En route / Mountains", 4: "Engine failure (v2)", 3: "Cargo (plane)", 
                              2: "Engine failure (v3)", 1: "Land / take off", 0: "Fire / explosion"
                             })

In [26]:
crashes['Cluster_name'] = crashes['Cluster'].apply(lambda x: topic_model.custom_labels_[x])
crashes.tail(2)

Date                                      Location  \
4829  2009-06-07  Near Port Hope Simpson, Newfoundland, Canada   
4830  2009-06-08             State of Arunachal Pradesh, India   

                         Operator                              Type  Aboard  \
4829                   Strait Air  Britten-Norman BN-2A-27 Islander     1.0   
4830  Military - Indian Air Force                     Antonov An-32    13.0   

      Fatalities  Ground  \
4829         1.0     0.0   
4830        13.0     0.0   

                                                                                                                     Summary  \
4829              The air ambulance crashed into hills while attempting to land in heavy fog about 4 miles from the airport.   
4830  The military transport went missing while en route and might have crashed due to heavy rain in the mountainous region.   

      Cluster          Cluster_name  
4829       13                   Fog  
4830       15  Disappeared en route

In [27]:
crashes.to_csv("data/clean_crashes.clustered_summary.csv", sep='\t')

In [50]:
topic_model.get_topic_info()

Topic  Count  \
0       0    424   
1       1    380   
2       2    359   
3       3    356   
4       4    356   
5       5    338   
6       6    307   
7       7    305   
8       8    288   
9       9    242   
10     10    225   
11     11    219   
12     12    210   
13     13    204   
14     14    133   
15     15    125   
16     16    118   
17     17    118   
18     18     82   
19     19     42   

                                                             Name  \
0             0_emergency landing_exploded_shortly takeoff_landed   
1                       1_pilot failure_safe altitude_flew_flying   
2   2_cause accident_accident_failure pilot_contributing accident   
3                    3_pilot failure_cargo_accident_lost altitude   
4        4_engine failure_crash_emergency landing_shortly takeoff   
5            5_crash landed_crash_mountainous terrain_mountainous   
6           6_pilot failed_landing attempt_pilot error_crew error   
7                              7_crash_accident_survived_crashing   
8      8_engine failure_cause accident_pilot failed_failure pilot   
9      9_landing attempt_pilot attempted_runway attempting_landed   
10           10_crash landed_severe turbulence_crash_thunderstorm   
11                   11_shortly takeoff_ocean_sank_engine failure   
12                  12_flew_pilot attempted_struck trees_rain fog   
13                          13_pilot error_flew_airborne_rain fog   
14                        14_failure pilot_pilots_landed_survived   
15                          15_disappeared_en route_route_missing   
16                     16_emergency landing_air force_landed_shot   
17                     17_helicopter_pilot failure_crash_accident   
18                             18_flew_flying_mountain_flying low   
19          19_crash landed_pilot failure_emergency landing_crash   

              CustomName  \
0       Fire / explosion   
1        Land / take off   
2    Engine failure (v3)   
3          Cargo (plane)   
4    Engine failure (v2)   
5   En route / Mountains   
6            Pilot error   
7                  Crash   
8         Engine failure   
9        Landing attempt   
10     Weather / landing   
11      Crashed into sea   
12    Weather conditions   
13                   Fog   
14      Midair collision   
15  Disappeared en route   
16             Shot down   
17            Helicopter   
18             Mountains   
19            Mail plane   

                                                                                                                                                     Representation  \
0                                    [emergency landing, exploded, shortly takeoff, landed, caught fire, explosion, crash, landing, survived, attempting emergency]   
1                                        [pilot failure, safe altitude, flew, flying, mountains, altitude, mountain, mountainous terrain, mountainous, error pilot]   
2                                             [cause accident, accident, failure pilot, contributing accident, stalled, maneuver, flying, caused, aborted, failure]   
3                         [pilot failure, cargo, accident, lost altitude, flew, runway attempting, contributing accident, pilot command, failure maintain, takeoff]   
4                                        [engine failure, crash, emergency landing, shortly takeoff, malfunction, fatigue, broke, forced landing, failure, engines]   
5                                                 [crash landed, crash, mountainous terrain, mountainous, mountains, mountain, terrain, survived, poor weather, mt]   
6                            [pilot failed, landing attempt, pilot error, crew error, landing approach, failure crew, pilots, flying, disoriented, missed approach]   
7                                                                        [crash, accident, survived, crashing, flying, pilot reported, pilots, died, jet, ran fuel]   
8   [engine failure, cause accident, pilo

# 5. Topic-Document Distribution

In [15]:
topic_distr, _ = topic_model.approximate_distribution(crashes.Summary.to_list(), window=8, stride=4)

100%|████████████████████████████████████████████████████████████████████████████████████| 5/5 [00:00<00:00,  8.00it/s]


In [16]:
# Visualize the topic-document distribution for a single document
index = 3
print(crashes.Summary.iloc[index])
topic_model.visualize_distribution(topic_distr[index], custom_labels=True)

The airship flew into a thunderstorm and encountered a severe downdraft crashing 20 miles north of Helgoland Island into the sea. The ship broke in two and the control car immediately sank drowning its occupants.


In [17]:
topic_model.visualize_hierarchy(custom_labels=True)

# 6. Visualization

In [9]:
reduced_embeddings = UMAP(n_neighbors=300, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [12]:
topic_model.visualize_documents(crashes.Summary, reduced_embeddings=reduced_embeddings, custom_labels=True)

In [11]:
topic_model.visualize_documents(crashes.Summary, reduced_embeddings=reduced_embeddings, 
                                custom_labels=True, hide_annotations=True)